In [2]:
import ast
import json
import math
import os
import numpy as np
import pandas as pd
from geopy.geocoders import Nominatim
import requests
import matplotlib.cm as cm
import matplotlib.colors as colors
from sklearn.cluster import KMeans
import folium

print('Libraries imported.')

pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)





Libraries imported.


In [14]:
clientId = 'FDW2QFJRIASQ2KIYJJHQ3QB11WDAYGNGFWZTWRBN4X2IHWOV'
clientSecret = 'HXHJDYCPW30RG1YTAXR3MC5SZ0M2OZR2LQPQULAPZB5SHODE'
version = '20180606'
limit = 500
radius = 500

address = 'Chicago'
geolocator = Nominatim(user_agent="chicago_explorer")
latitude = 41.8114215
longitude = -87.7261651
try:
    location = geolocator.geocode(address)
    latitude = location.latitude
    longitude = location.longitude
    print('The geograpical coordinate of {} City are {}, {}.'.format(address, latitude, longitude))
except Exception as e:
    print(e)
    
url = 'https://en.wikipedia.org/wiki/List_of_neighborhoods_in_Chicago'
data = requests.get(url, verify=False)
tables = pd.read_html(data.text)
PostalCode_df = pd.DataFrame(tables[0])
print(PostalCode_df['Neighborhood'])

#match coordinates using nominatim
nom = Nominatim()
PostalCode_df["Coordinates"] = PostalCode_df["Neighborhood"].apply(nom.geocode)
PostalCode_df["Latitude"] = PostalCode_df["Coordinates"].apply(lambda x: x.latitude if x != None else None)
PostalCode_df["Longitude"] = PostalCode_df["Coordinates"].apply(lambda x: x.longitude if x != None else None)
PostalCode_df.rename(columns={'Neighborhood': 'Borough', 'Community area': 'Neighborhood'}, inplace=True)
print(PostalCode_df)



The geograpical coordinate of Chicago City are 41.8755616, -87.6244212.


C:\ProgramData\Anaconda3\lib\site-packages\urllib3\connectionpool.py:847: InsecureRequestWarning: Unverified HTTPS request is being made. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#ssl-warnings
  InsecureRequestWarning)
C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:26: DeprecationWarning: Using Nominatim with the default "geopy/1.20.0" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.


0                              Albany Park
1                          Altgeld Gardens
2                            Andersonville
3                           Archer Heights
4                            Armour Square
5                                  Ashburn
6                          Ashburn Estates
7                           Auburn Gresham
8                              Avalon Park
9                                 Avondale
10                        Avondale Gardens
11                       Back of the Yards
12                         Belmont Central
13                         Belmont Gardens
14                         Belmont Heights
15                         Belmont Terrace
16                                 Beverly
17                            Beverly View
18                           Beverly Woods
19                                Big Oaks
20                                Boystown
21                             Bowmanville
22                                Brainerd
23         

                                 Borough             Neighborhood  \
0                            Albany Park              Albany Park   
1                        Altgeld Gardens                Riverdale   
2                          Andersonville                Edgewater   
3                         Archer Heights           Archer Heights   
4                          Armour Square            Armour Square   
5                                Ashburn                  Ashburn   
6                        Ashburn Estates                  Ashburn   
7                         Auburn Gresham           Auburn Gresham   
8                            Avalon Park              Avalon Park   
9                               Avondale                 Avondale   
10                      Avondale Gardens              Irving Park   
11                     Back of the Yards                 New City   
12                       Belmont Central           Belmont Cragin   
13                       Belmont G

In [16]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    venues_list = []
    print("working on your stuff")
    for name, lat, lng in zip(names, latitudes, longitudes):
        #get venue and interesting places nearby using foursquare api
        try:
            url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(clientId, clientSecret, version, lat, lng, radius, limit)
            result = requests.get(url)
            #In case of 400 or error, ignore the reponse and continue to next
            if 'warning' in result.json()['response']:
                print("warning")
            elif result.status_code == 400:
                print("warning")
            else:
                results = result.json()["response"]['groups'][0]['items']
                print(results)
                venues_list.append([(name, lat, lng, v['venue']['name'], v['venue']['location']['lat'], v['venue']['location']['lng'], v['venue']['categories'][0]['name']) for v in results])
        except Exception as e:
            print(e)
    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 'Neighborhood Latitude', 'Neighborhood Longitude', 'Venue', 'Venue Latitude', 'Venue Longitude', 'Venue Category']

    return (nearby_venues)



In [17]:
venues = getNearbyVenues(names=PostalCode_df['Neighborhood'], latitudes=PostalCode_df['Latitude'], longitudes=PostalCode_df['Longitude'])
print(venues.shape)
venues.groupby('Neighborhood').count()

working on your stuff
[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4ab82e65f964a5207c7c20e3', 'name': 'Chicago Produce', 'location': {'address': '3500 W Lawrence Ave', 'crossStreet': 'at N Drake Ave', 'lat': 41.97055281291674, 'lng': -87.7163271937518, 'labeledLatLngs': [{'label': 'display', 'lat': 41.97055281291674, 'lng': -87.7163271937518}], 'distance': 154, 'postalCode': '60625', 'cc': 'US', 'city': 'Chicago', 'state': 'IL', 'country': 'United States', 'formattedAddress': ['3500 W Lawrence Ave (at N Drake Ave)', 'Chicago, IL 60625', 'United States']}, 'categories': [{'id': '4bf58dd8d48988d118951735', 'name': 'Grocery Store', 'pluralName': 'Grocery Stores', 'shortName': 'Grocery Store', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/shops/food_grocery_', 'suffix': '.png'}, 'primary': True}], 'photos': {'count': 0, 'groups': []}}, 'referralId': 'e-0-4ab82e65f964a5207

warning
[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '53488330498ead4f0c0e675d', 'name': 'Anderson Station', 'location': {'lat': 32.194683, 'lng': -84.139898, 'labeledLatLngs': [{'label': 'display', 'lat': 32.194683, 'lng': -84.139898}], 'distance': 146, 'cc': 'US', 'city': 'Andersonville', 'state': 'GA', 'country': 'United States', 'formattedAddress': ['Andersonville, GA', 'United States']}, 'categories': [{'id': '4bf58dd8d48988d14e941735', 'name': 'American Restaurant', 'pluralName': 'American Restaurants', 'shortName': 'American', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/default_', 'suffix': '.png'}, 'primary': True}], 'photos': {'count': 0, 'groups': []}}, 'referralId': 'e-0-53488330498ead4f0c0e675d-0'}, {'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '51

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4e569dd6922e68c545c270de', 'name': "Ferro's Italian Sandwiches", 'location': {'address': '200 W 31st St', 'lat': 41.838424118851755, 'lng': -87.6320440168474, 'labeledLatLngs': [{'label': 'display', 'lat': 41.838424118851755, 'lng': -87.6320440168474}], 'distance': 199, 'postalCode': '60616', 'cc': 'US', 'city': 'Chicago', 'state': 'IL', 'country': 'United States', 'formattedAddress': ['200 W 31st St', 'Chicago, IL 60616', 'United States']}, 'categories': [{'id': '4bf58dd8d48988d1c5941735', 'name': 'Sandwich Place', 'pluralName': 'Sandwich Places', 'shortName': 'Sandwiches', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/deli_', 'suffix': '.png'}, 'primary': True}], 'photos': {'count': 0, 'groups': []}}, 'referralId': 'e-0-4e569dd6922e68c545c270de-0'}, {'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4bb3cb732397b7131da338b3', 'name': 'Carolina Brothers Pit Barbeque', 'location': {'address': '20702 Ashburn Rd', 'lat': 39.0437590782225, 'lng': -77.48719298898324, 'labeledLatLngs': [{'label': 'display', 'lat': 39.0437590782225, 'lng': -77.48719298898324}], 'distance': 26, 'postalCode': '20147', 'cc': 'US', 'city': 'Ashburn', 'state': 'VA', 'country': 'United States', 'formattedAddress': ['20702 Ashburn Rd', 'Ashburn, VA 20147', 'United States']}, 'categories': [{'id': '4bf58dd8d48988d1df931735', 'name': 'BBQ Joint', 'pluralName': 'BBQ Joints', 'shortName': 'BBQ', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/bbqalt_', 'suffix': '.png'}, 'primary': True}], 'photos': {'count': 0, 'groups': []}}, 'referralId': 'e-0-4bb3cb732397b7131da338b3-0'}, {'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4c0ca34c336220a19a87c977', 'name': "Nick's Gyros", 'location': {'address': '7856 S Ashland Ave', 'crossStreet': 'at 79th St.', 'lat': 41.750500584873095, 'lng': -87.66367557574944, 'labeledLatLngs': [{'label': 'display', 'lat': 41.750500584873095, 'lng': -87.66367557574944}], 'distance': 52, 'postalCode': '60620', 'cc': 'US', 'city': 'Chicago', 'state': 'IL', 'country': 'United States', 'formattedAddress': ['7856 S Ashland Ave (at 79th St.)', 'Chicago, IL 60620', 'United States']}, 'categories': [{'id': '4bf58dd8d48988d10e941735', 'name': 'Greek Restaurant', 'pluralName': 'Greek Restaurants', 'shortName': 'Greek', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/greek_', 'suffix': '.png'}, 'primary': True}], 'delivery': {'id': '961081', 'url': 'https://www.grubhub.com/restaurant/nicks-gyros-7858-s-ashland-ave-chicago/9610

...

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4c69cd5ec946e21e5e34eb8e', 'name': 'KFC', 'location': {'address': '6732 N Western Ave', 'crossStreet': 'Dodge Ave', 'lat': 42.00428467400814, 'lng': -87.69038580183508, 'labeledLatLngs': [{'label': 'display', 'lat': 42.00428467400814, 'lng': -87.69038580183508}], 'distance': 491, 'postalCode': '60645', 'cc': 'US', 'city': 'Chicago', 'state': 'IL', 'country': 'United States', 'formattedAddress': ['6732 N Western Ave (Dodge Ave)', 'Chicago, IL 60645', 'United States']}, 'categories': [{'id': '4d4ae6fc7a7b7dea34424761', 'name': 'Fried Chicken Joint', 'pluralName': 'Fried Chicken Joints', 'shortName': 'Fried Chicken', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/friedchicken_', 'suffix': '.png'}, 'primary': True}], 'delivery': {'id': '921700', 'url': 'https://www.grubhub.com/restaurant/kfc-6732-n-western-ave-chicago/92170

warning
[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '541c39ff498ee385598bdfff', 'name': "Dove's Luncheonette", 'location': {'address': '1545 N Damen Ave', 'crossStreet': 'btwn Milwaukee Ave & Wicker Park Ave', 'lat': 41.90952359487261, 'lng': -87.67744655553935, 'labeledLatLngs': [{'label': 'display', 'lat': 41.90952359487261, 'lng': -87.67744655553935}], 'distance': 200, 'postalCode': '60622', 'cc': 'US', 'neighborhood': 'Wicker Park', 'city': 'Chicago', 'state': 'IL', 'country': 'United States', 'formattedAddress': ['1545 N Damen Ave (btwn Milwaukee Ave & Wicker Park Ave)', 'Chicago, IL 60622', 'United States']}, 'categories': [{'id': '4bf58dd8d48988d147941735', 'name': 'Diner', 'pluralName': 'Diners', 'shortName': 'Diner', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/diner_', 'suffix': '.png'}, 'primary': True}], 'delivery': {'id': '758386', 'url': 'https://w

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4d127176d0fda093eaedab57', 'name': 'B&B Wildwood 10', 'location': {'address': '16820 Main St', 'crossStreet': 'at Taylor Rd', 'lat': 38.580712, 'lng': -90.629763, 'labeledLatLngs': [{'label': 'display', 'lat': 38.580712, 'lng': -90.629763}], 'distance': 127, 'postalCode': '63040', 'cc': 'US', 'city': 'Wildwood', 'state': 'MO', 'country': 'United States', 'formattedAddress': ['16820 Main St (at Taylor Rd)', 'Wildwood, MO 63040', 'United States']}, 'categories': [{'id': '4bf58dd8d48988d17f941735', 'name': 'Movie Theater', 'pluralName': 'Movie Theaters', 'shortName': 'Movie Theater', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/arts_entertainment/movietheater_', 'suffix': '.png'}, 'primary': True}], 'events': {'count': 12, 'summary': '12 movies'}, 'photos': {'count': 0, 'groups': []}}, 'referralId': 'e-0-4d127176d0fda093eaeda

warning
[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '4ae27e2cf964a5209e8e21e3', 'name': 'Grizzly Cafe', 'location': {'address': '1455 State Highway 2', 'crossStreet': 'btw Willow and Elm', 'lat': 34.35936878739532, 'lng': -117.63014902095463, 'labeledLatLngs': [{'label': 'display', 'lat': 34.35936878739532, 'lng': -117.63014902095463}], 'distance': 260, 'postalCode': '92397', 'cc': 'US', 'city': 'Wrightwood', 'state': 'CA', 'country': 'United States', 'formattedAddress': ['1455 State Highway 2 (btw Willow and Elm)', 'Wrightwood, CA 92397', 'United States']}, 'categories': [{'id': '4bf58dd8d48988d14e941735', 'name': 'American Restaurant', 'pluralName': 'American Restaurants', 'shortName': 'American', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/default_', 'suffix': '.png'}, 'primary': True}], 'photos': {'count': 0, 'groups': []}}, 'referralId': 'e-0-4ae27e2cf964a

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                                   
Albany Park                               137                     137    137   
Archer Heights                             25                      25     25   
Armour Square                             147                     147    147   
Ashburn                                    24                      24     24   
Auburn Gresham                             56                      56     56   
Austin, Humboldt Park                       9                       9      9   
Avalon Park                                26                      26     26   
Avondale, Irving Park                      20                      20     20   
Belmont Cragin                             36                      36     36   
Beverly                                    28                      28     28   
Bridgeport                                  4                       4      4   
Brighton Park                              17                      17     17   
Burnside                                    4                       4      4   
Calumet Heights                            33                      33     33   
Chatham                                    17                      17     17   
Chicago Lawn                               54                      54     54   
Clearing                                   24                      24     24   
Douglas                                    74                      74     74   
Dunning                                    76                      76     76   
East Garfield Park                         12                      12     12   
East Side                                   5                       5      5   
Edgewater                                  73                      73     73   
Edison Park                                27                      27     27   
Englewood                                  34                      34     34   
Forest Glen                                55                      55     55   
Fuller Park                                 5                       5      5   
Gage Park                                  10                      10     10   
Garfield Ridge                             32                      32     32   
Grand Boulevard                            16                      16     16   
Greater Grand Crossing                     11                      11     11   
Hegewisch                                   7                       7      7   
Hermosa                                    38                      38     38   
Humboldt Park                               9                       9      9   
Hyde Park                                   5                       5      5   
Irving Park                                49                      49     49   
Jefferson Park                             31                      31     31   
Kenwood                                    26                      26     26   
Lake View                                  32                      32     32   
Lincoln Park                               31                      31     31   
Lincoln Square                            199                     199    199   
Logan Square                               96                      96     96   
Lower West Side                           251                     251    251   
McKinley Park                              18                      18     18   
Montclare                                  15                      15     15   
Morgan Park                                12                      12     12   
Near North Side                           372                     372    372   
Near South Side                           214                     214    214   
Near West Side                            348                     348    348   
New City                

In [18]:
def returnMostCommonVenues(row, num_top_venues):
    #find most common venue and return
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)

    return row_categories_sorted.index.values[0:num_top_venues]

In [19]:


oneHotEncoding = pd.get_dummies(venues[['Venue Category']], prefix="", prefix_sep="")

    # add neighborhood column back to dataframe
oneHotEncoding['Neighborhood'] = venues['Neighborhood']

    # move neighborhood column to the first column
fixedColumns = [oneHotEncoding.columns[-1]] + list(oneHotEncoding.columns[:-1])
oneHotEncoding = oneHotEncoding[fixedColumns]

grouped = oneHotEncoding.groupby('Neighborhood').mean().reset_index()

countOfTopVenues = 5

for hood in grouped['Neighborhood']:
    print("----" + hood + "----")
    temp = grouped[grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue', 'freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(countOfTopVenues))
    print('\n')

countOfTopVenues = 10

indicators = ['st', 'nd', 'rd']

    # create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(countOfTopVenues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind + 1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind + 1))

    # create a new dataframe
sortedNeighborhoodVenues = pd.DataFrame(columns=columns)
sortedNeighborhoodVenues['Neighborhood'] = grouped['Neighborhood']

print("here")
for ind in np.arange(grouped.shape[0]):
    sortedNeighborhoodVenues.iloc[ind, 1:] = returnMostCommonVenues(grouped.iloc[ind, :], countOfTopVenues)

    # set number of clusters
kClusters = 3

groupedCluster = grouped.drop('Neighborhood', 1)

    # run k-means clustering
kmeans = KMeans(n_clusters=kClusters, random_state=0).fit(groupedCluster)

    # check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]
print("again here")
    # add clustering labels
sortedNeighborhoodVenues.insert(0, 'ClusterLabels', kmeans.labels_)

merged = PostalCode_df
print(merged)
merged = merged.join(sortedNeighborhoodVenues.set_index('Neighborhood'), on='Neighborhood')

merged = merged.dropna()
merged["ClusterLabels"] = merged.ClusterLabels.astype(int)

    # create map
mapClusters = folium.Map(location=[latitude, longitude], zoom_start=11)

    # set color scheme for the clusters
x = np.arange(kClusters)
ys = [i + x + (i * x) ** 2 for i in range(kClusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]
print("almost done dana done")

    # add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(merged['Latitude'], merged['Longitude'], merged['Neighborhood'], merged['ClusterLabels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker([lat, lon], radius=5, popup=label, color=rainbow[cluster - 1], fill=True, fill_color=rainbow[cluster - 1], fill_opacity=0.7).add_to(mapClusters)

mapClusters.save("demo.html")


----Albany Park----
               venue  freq
0        Art Gallery  0.06
1     Clothing Store  0.06
2           Boutique  0.06
3        Coffee Shop  0.04
4  French Restaurant  0.04


----Archer Heights----
                venue  freq
0  Mexican Restaurant  0.12
1   Mobile Phone Shop  0.12
2       Grocery Store  0.08
3                Park  0.08
4         Gas Station  0.08


----Armour Square----
                venue  freq
0  Chinese Restaurant  0.12
1              Bakery  0.06
2  Italian Restaurant  0.06
3                Café  0.06
4    Asian Restaurant  0.03


----Ashburn----
              venue  freq
0             Hotel  0.12
1  Business Service  0.08
2               Bar  0.08
3         BBQ Joint  0.08
4               Zoo  0.04


----Auburn Gresham----
                    venue  freq
0  Furniture / Home Store  0.07
1    Fast Food Restaurant  0.05
2          Cosmetics Shop  0.05
3       Mobile Phone Shop  0.05
4       Accessories Store  0.04


----Austin, Humboldt Park----
          

                 venue  freq
0                Hotel  0.05
1   Italian Restaurant  0.05
2  American Restaurant  0.04
3          Coffee Shop  0.04
4           Restaurant  0.03


----Near South Side----
                 venue  freq
0       History Museum  0.07
1             Aquarium  0.05
2                 Park  0.04
3                Hotel  0.04
4  American Restaurant  0.03


----Near West Side----
                    venue  freq
0             Coffee Shop  0.06
1          Sandwich Place  0.05
2                   Hotel  0.03
3  Furniture / Home Store  0.03
4      Italian Restaurant  0.03


----New City----
                venue  freq
0         Pizza Place  0.11
1                Bank  0.09
2  Mexican Restaurant  0.07
3       Grocery Store  0.04
4          Shoe Store  0.04


----North Center----
         venue  freq
0          Bar  0.07
1  Coffee Shop  0.04
2  Bus Station  0.04
3      Brewery  0.04
4  Beer Garden  0.02


----North Lawndale----
                  venue  freq
0                 

In [9]:
url1 = 'https://www.rentcafe.com/average-rent-market-trends/us/il/chicago/'
data1 = requests.get(url1, verify=True)
tables1 = pd.read_html(data1.text)
Rent_df = pd.DataFrame(tables1[2])
Rent_df = Rent_df.loc[:, ['Average Rent', 'Average Rent.1']]
Rent_df.rename(columns={'Average Rent': 'Neighborhood', 'Average Rent.1': 'AverageRent'}, inplace=True)
Rent_df = Rent_df.drop([0])
Rent_df.reset_index()

dummy = pd.merge(merged, Rent_df, on='Neighborhood')
dummy.head()
#print("HELLO WORLD")
#Rent_df.head()


Borough Neighborhood  \
0       Albany Park  Albany Park   
1           Mayfair  Albany Park   
2     North Mayfair  Albany Park   
3  Ravenswood Manor  Albany Park   
4   Altgeld Gardens    Riverdale   

                                         Coordinates   Latitude   Longitude  \
0  (Albany Park, Chicago, Cook County, Illinois, ...  41.971937  -87.716174   
1  (Mayfair, City of Westminster, London, Greater...  51.511087   -0.147058   
2  (North Mayfair, Hidden Groves, Mesa, Maricopa ...  33.428116 -111.754851   
3  (Ravenswood Manor, Roscoe Village, Chicago, Co...  41.964622  -87.701380   
4  (Altgeld Gardens, Chicago, Cook County, Illino...  41.654864  -87.600446   

   ClusterLabels 1st Most Common Venue 2nd Most Common Venue  \
0              2           Art Gallery              Boutique   
1              2           Art Gallery              Boutique   
2              2           Art Gallery              Boutique   
3              2           Art Gallery              Boutique   
4              1        Scenic Lookout                  Pier   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0        Clothing Store     French Restaurant           Coffee Shop   
1        Clothing Store     French Restaurant           Coffee Shop   
2        Clothing Store     French Restaurant           Coffee Shop   
3        Clothing Store     French Restaurant           Coffee Shop   
4                  Park       Harbor / Marina                 Trail   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0          Cocktail Bar             Hotel Bar                 Hotel   
1          Cocktail Bar             Hotel Bar                 Hotel   
2          Cocktail Bar             Hotel Bar                 Hotel   
3          Cocktail Bar             Hotel Bar                 Hotel   
4           Supermarket         Historic Site     Fish & Chips Shop   

  9th Most Common Venue 10th Most Common Venue AverageRent  
0                Bakery                   Café      $1,193  
1                Bakery                   Café      $1,193  
2                Bakery                   Café      $1,193  
3                Bakery                   Café      $1,193  
4            Playground          Grocery Store        $612

In [10]:
newData = []
for lat, lon, point, one, two, three, four, five, six, seven, eight, nine, ten, rent in zip(dummy['Latitude'], dummy['Longitude'], dummy['Neighborhood'], dummy['1st Most Common Venue'], dummy['2nd Most Common Venue'], dummy['3rd Most Common Venue'], dummy['4th Most Common Venue'], dummy['5th Most Common Venue'], dummy['6th Most Common Venue'], dummy['7th Most Common Venue'], dummy['8th Most Common Venue'], dummy['9th Most Common Venue'], dummy['10th Most Common Venue'], dummy['AverageRent']):
    if not math.isnan(lat):
        if type(one) is str:
            temp = {}
            temp['lat'] = lat
            temp['lon'] = lon
            temp['rent'] = rent
            temp['point'] = point
            newData.append(temp)
colordict = {0: 'lightblue', 1: 'lightgreen', 2: 'orange', 3: 'red'}
mapClusters = folium.Map(location=[latitude, longitude], zoom_start=11)
for element in newData:
        color = colordict[3]
        rents = element['rent'].strip('$')
        rent = int(rents.replace(',',''))
        if rent <= 600:
            color = colordict[1]
        elif rent > 600 and rent <= 1000:
            color = colordict[0]
        elif rent > 1000 and rent <= 1500:
            color = colordict[2]
        else:
            color = colordict[3]
        lat = element['lat']
        lon = element['lon']
        label = folium.Popup(str(element['point']) + ' Rent ' + str(element['rent']), parse_html=True)
        folium.CircleMarker([lat, lon], radius=7, popup=label, fill=True, fill_color=color, fill_opacity=0.7).add_to(mapClusters)

mapClusters.save("png.html")

In [35]:
def getRestaurantInfo(names, latitudes, longitudes, radius=500):
    for name, lat, lng in zip(names, latitudes, longitudes):
        #get venue and interesting places nearby using foursquare api
        try:
            search_query = 'Restaurant'
            radius = 500
            url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{}&v={}&query={}&radius={}&limit={}'.format(clientId, clientSecret, latitude, longitude, version, search_query, radius, 30)
            result = requests.get(url)
            print(result.json())
            with open("Restaurant_venues.json", "w") as f:
                f.write(str(result.json()))
            f.close()
        except Exception as e:
            print(e)
getRestaurantInfo(names = dummy['Neighborhood'], latitudes = dummy['Latitude'], longitudes = dummy['Longitude'], radius=500)



{'meta': {'code': 200, 'requestId': '5d0f6044bcbf7a003978f242'}, 'response': {'venues': [{'id': '4b2bedd4f964a520e6bd24e3', 'name': 'The Berghoff Restaurant', 'location': {'address': '17 W Adams St', 'crossStreet': 'btwn S Dearborn St & S State St', 'lat': 41.879334126547164, 'lng': -87.62836809709047, 'labeledLatLngs': [{'label': 'display', 'lat': 41.879334126547164, 'lng': -87.62836809709047}], 'distance': 532, 'postalCode': '60603', 'cc': 'US', 'city': 'Chicago', 'state': 'IL', 'country': 'United States', 'formattedAddress': ['17 W Adams St (btwn S Dearborn St & S State St)', 'Chicago, IL 60603', 'United States']}, 'categories': [{'id': '4bf58dd8d48988d10d941735', 'name': 'German Restaurant', 'pluralName': 'German Restaurants', 'shortName': 'German', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/german_', 'suffix': '.png'}, 'primary': True}], 'venuePage': {'id': '90487382'}, 'referralId': 'v-1561288772', 'hasPerk': False}, {'id': '4b9ad8c5f964a520ccdb35e3', 'name':

{'meta': {'code': 200, 'requestId': '5d0f60446f0aa2002cf08164'}, 'response': {'venues': [{'id': '4b2bedd4f964a520e6bd24e3', 'name': 'The Berghoff Restaurant', 'location': {'address': '17 W Adams St', 'crossStreet': 'btwn S Dearborn St & S State St', 'lat': 41.879334126547164, 'lng': -87.62836809709047, 'labeledLatLngs': [{'label': 'display', 'lat': 41.879334126547164, 'lng': -87.62836809709047}], 'distance': 532, 'postalCode': '60603', 'cc': 'US', 'city': 'Chicago', 'state': 'IL', 'country': 'United States', 'formattedAddress': ['17 W Adams St (btwn S Dearborn St & S State St)', 'Chicago, IL 60603', 'United States']}, 'categories': [{'id': '4bf58dd8d48988d10d941735', 'name': 'German Restaurant', 'pluralName': 'German Restaurants', 'shortName': 'German', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/german_', 'suffix': '.png'}, 'primary': True}], 'venuePage': {'id': '90487382'}, 'referralId': 'v-1561288772', 'hasPerk': False}, {'id': '4b9ad8c5f964a520ccdb35e3', 'name':

{'meta': {'code': 200, 'requestId': '5d0f6044fd16bb002c2a766e'}, 'response': {'venues': [{'id': '4b2bedd4f964a520e6bd24e3', 'name': 'The Berghoff Restaurant', 'location': {'address': '17 W Adams St', 'crossStreet': 'btwn S Dearborn St & S State St', 'lat': 41.879334126547164, 'lng': -87.62836809709047, 'labeledLatLngs': [{'label': 'display', 'lat': 41.879334126547164, 'lng': -87.62836809709047}], 'distance': 532, 'postalCode': '60603', 'cc': 'US', 'city': 'Chicago', 'state': 'IL', 'country': 'United States', 'formattedAddress': ['17 W Adams St (btwn S Dearborn St & S State St)', 'Chicago, IL 60603', 'United States']}, 'categories': [{'id': '4bf58dd8d48988d10d941735', 'name': 'German Restaurant', 'pluralName': 'German Restaurants', 'shortName': 'German', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/german_', 'suffix': '.png'}, 'primary': True}], 'venuePage': {'id': '90487382'}, 'referralId': 'v-1561288772', 'hasPerk': False}, {'id': '4b9ad8c5f964a520ccdb35e3', 'name':

{'meta': {'code': 200, 'requestId': '5d0f6045c53093002c06fbd4'}, 'response': {'venues': [{'id': '4b2bedd4f964a520e6bd24e3', 'name': 'The Berghoff Restaurant', 'location': {'address': '17 W Adams St', 'crossStreet': 'btwn S Dearborn St & S State St', 'lat': 41.879334126547164, 'lng': -87.62836809709047, 'labeledLatLngs': [{'label': 'display', 'lat': 41.879334126547164, 'lng': -87.62836809709047}], 'distance': 532, 'postalCode': '60603', 'cc': 'US', 'city': 'Chicago', 'state': 'IL', 'country': 'United States', 'formattedAddress': ['17 W Adams St (btwn S Dearborn St & S State St)', 'Chicago, IL 60603', 'United States']}, 'categories': [{'id': '4bf58dd8d48988d10d941735', 'name': 'German Restaurant', 'pluralName': 'German Restaurants', 'shortName': 'German', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/german_', 'suffix': '.png'}, 'primary': True}], 'venuePage': {'id': '90487382'}, 'referralId': 'v-1561288773', 'hasPerk': False}, {'id': '4b9ad8c5f964a520ccdb35e3', 'name':

{'meta': {'code': 200, 'requestId': '5d0f6045bbf1bd00230785b6'}, 'response': {'venues': [{'id': '4b2bedd4f964a520e6bd24e3', 'name': 'The Berghoff Restaurant', 'location': {'address': '17 W Adams St', 'crossStreet': 'btwn S Dearborn St & S State St', 'lat': 41.879334126547164, 'lng': -87.62836809709047, 'labeledLatLngs': [{'label': 'display', 'lat': 41.879334126547164, 'lng': -87.62836809709047}], 'distance': 532, 'postalCode': '60603', 'cc': 'US', 'city': 'Chicago', 'state': 'IL', 'country': 'United States', 'formattedAddress': ['17 W Adams St (btwn S Dearborn St & S State St)', 'Chicago, IL 60603', 'United States']}, 'categories': [{'id': '4bf58dd8d48988d10d941735', 'name': 'German Restaurant', 'pluralName': 'German Restaurants', 'shortName': 'German', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/german_', 'suffix': '.png'}, 'primary': True}], 'venuePage': {'id': '90487382'}, 'referralId': 'v-1561288773', 'hasPerk': False}, {'id': '4b9ad8c5f964a520ccdb35e3', 'name':

...

{'meta': {'code': 200, 'requestId': '5d0f606caf35f30025a461ec'}, 'response': {'venues': [{'id': '4b2bedd4f964a520e6bd24e3', 'name': 'The Berghoff Restaurant', 'location': {'address': '17 W Adams St', 'crossStreet': 'btwn S Dearborn St & S State St', 'lat': 41.879334126547164, 'lng': -87.62836809709047, 'labeledLatLngs': [{'label': 'display', 'lat': 41.879334126547164, 'lng': -87.62836809709047}], 'distance': 532, 'postalCode': '60603', 'cc': 'US', 'city': 'Chicago', 'state': 'IL', 'country': 'United States', 'formattedAddress': ['17 W Adams St (btwn S Dearborn St & S State St)', 'Chicago, IL 60603', 'United States']}, 'categories': [{'id': '4bf58dd8d48988d10d941735', 'name': 'German Restaurant', 'pluralName': 'German Restaurants', 'shortName': 'German', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/german_', 'suffix': '.png'}, 'primary': True}], 'venuePage': {'id': '90487382'}, 'referralId': 'v-1561288812', 'hasPerk': False}, {'id': '4b9ad8c5f964a520ccdb35e3', 'name':

{'meta': {'code': 200, 'requestId': '5d0f606d6c0aa50023509ffb'}, 'response': {'venues': [{'id': '4b2bedd4f964a520e6bd24e3', 'name': 'The Berghoff Restaurant', 'location': {'address': '17 W Adams St', 'crossStreet': 'btwn S Dearborn St & S State St', 'lat': 41.879334126547164, 'lng': -87.62836809709047, 'labeledLatLngs': [{'label': 'display', 'lat': 41.879334126547164, 'lng': -87.62836809709047}], 'distance': 532, 'postalCode': '60603', 'cc': 'US', 'city': 'Chicago', 'state': 'IL', 'country': 'United States', 'formattedAddress': ['17 W Adams St (btwn S Dearborn St & S State St)', 'Chicago, IL 60603', 'United States']}, 'categories': [{'id': '4bf58dd8d48988d10d941735', 'name': 'German Restaurant', 'pluralName': 'German Restaurants', 'shortName': 'German', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/german_', 'suffix': '.png'}, 'primary': True}], 'venuePage': {'id': '90487382'}, 'referralId': 'v-1561288813', 'hasPerk': False}, {'id': '4b9ad8c5f964a520ccdb35e3', 'name':

{'meta': {'code': 200, 'requestId': '5d0f606de0c0c9002c3d2973'}, 'response': {'venues': [{'id': '4b2bedd4f964a520e6bd24e3', 'name': 'The Berghoff Restaurant', 'location': {'address': '17 W Adams St', 'crossStreet': 'btwn S Dearborn St & S State St', 'lat': 41.879334126547164, 'lng': -87.62836809709047, 'labeledLatLngs': [{'label': 'display', 'lat': 41.879334126547164, 'lng': -87.62836809709047}], 'distance': 532, 'postalCode': '60603', 'cc': 'US', 'city': 'Chicago', 'state': 'IL', 'country': 'United States', 'formattedAddress': ['17 W Adams St (btwn S Dearborn St & S State St)', 'Chicago, IL 60603', 'United States']}, 'categories': [{'id': '4bf58dd8d48988d10d941735', 'name': 'German Restaurant', 'pluralName': 'German Restaurants', 'shortName': 'German', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/german_', 'suffix': '.png'}, 'primary': True}], 'venuePage': {'id': '90487382'}, 'referralId': 'v-1561288813', 'hasPerk': False}, {'id': '4b9ad8c5f964a520ccdb35e3', 'name':

{'meta': {'code': 200, 'requestId': '5d0f606dad1789002ce941e8'}, 'response': {'venues': [{'id': '4b2bedd4f964a520e6bd24e3', 'name': 'The Berghoff Restaurant', 'location': {'address': '17 W Adams St', 'crossStreet': 'btwn S Dearborn St & S State St', 'lat': 41.879334126547164, 'lng': -87.62836809709047, 'labeledLatLngs': [{'label': 'display', 'lat': 41.879334126547164, 'lng': -87.62836809709047}], 'distance': 532, 'postalCode': '60603', 'cc': 'US', 'city': 'Chicago', 'state': 'IL', 'country': 'United States', 'formattedAddress': ['17 W Adams St (btwn S Dearborn St & S State St)', 'Chicago, IL 60603', 'United States']}, 'categories': [{'id': '4bf58dd8d48988d10d941735', 'name': 'German Restaurant', 'pluralName': 'German Restaurants', 'shortName': 'German', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/german_', 'suffix': '.png'}, 'primary': True}], 'venuePage': {'id': '90487382'}, 'referralId': 'v-1561288814', 'hasPerk': False}, {'id': '4b9ad8c5f964a520ccdb35e3', 'name':

{'meta': {'code': 200, 'requestId': '5d0f606ee9b9a50025d69203'}, 'response': {'venues': [{'id': '4b2bedd4f964a520e6bd24e3', 'name': 'The Berghoff Restaurant', 'location': {'address': '17 W Adams St', 'crossStreet': 'btwn S Dearborn St & S State St', 'lat': 41.879334126547164, 'lng': -87.62836809709047, 'labeledLatLngs': [{'label': 'display', 'lat': 41.879334126547164, 'lng': -87.62836809709047}], 'distance': 532, 'postalCode': '60603', 'cc': 'US', 'city': 'Chicago', 'state': 'IL', 'country': 'United States', 'formattedAddress': ['17 W Adams St (btwn S Dearborn St & S State St)', 'Chicago, IL 60603', 'United States']}, 'categories': [{'id': '4bf58dd8d48988d10d941735', 'name': 'German Restaurant', 'pluralName': 'German Restaurants', 'shortName': 'German', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/german_', 'suffix': '.png'}, 'primary': True}], 'venuePage': {'id': '90487382'}, 'referralId': 'v-1561288814', 'hasPerk': False}, {'id': '4b9ad8c5f964a520ccdb35e3', 'name':

In [23]:
def getRestaurantInfo(names, latitudes, longitudes, radius=500):
    for name, lat, lng in zip(names, latitudes, longitudes):
        #get venue and interesting places nearby using foursquare api
        try:
            search_query = 'vegan food'
            radius = 500
            url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{}&v={}&query={}&radius={}&limit={}'.format(clientId, clientSecret, latitude, longitude, version, search_query, radius, 30)
            result = requests.get(url)
            print(result.json())
            with open("vegan_venues.json", "w") as f:
                f.write(str(result.json()))
            f.close()
        except Exception as e:
            print(e)
getRestaurantInfo(names = dummy['Neighborhood'], latitudes = dummy['Latitude'], longitudes = dummy['Longitude'], radius=500)

def getVenueRating():
    with open("vegan_venues.json", "r") as f:
        dummy = f.read()
    f.close()
    json_data = ast.literal_eval(dummy)
    ping = json.dumps(json_data)
    pong = json.loads(ping)
    venues = pong['response']['venues']
    out = []
    for venue in venues:
        venueMap = {}
        venueMap['id'] = venue['id']
        venueMap['name'] = venue['name']
        venueMap['type'] = venue['categories'][0]['name']
        venueMap['address'] = venue['location']
        venueId = venue['id']
        url = 'https://api.foursquare.com/v2/venues/{}?client_id={}&client_secret={}&v={}'.format(venueId, clientId, clientSecret, version)
        result = requests.get(url)
        ratingJson = result.json()
        check = ratingJson['response']['venue']
        if 'rating' in check:
            print(ratingJson['response']['venue']['rating'])
            venueMap['rating'] = ratingJson['response']['venue']['rating']
        else:
            print("no rating")
            venueMap['rating'] = 'NA'
        out.append(venueMap)
    print(out)
    with open("rating.json", "w") as ratingFile:
        ratingFile.write(str(out))
    ratingFile.close()

getVenueRating()

{'meta': {'code': 200, 'requestId': '5d113c4f787dba00387ae6cb'}, 'response': {'venues': [{'id': '54659f6f498e137569427d36', 'name': 'Metra  Food Court', 'location': {'address': 'Citigroup Center', 'crossStreet': '500 West Madison Street', 'lat': 41.875440756396515, 'lng': -87.62467861175537, 'labeledLatLngs': [{'label': 'display', 'lat': 41.875440756396515, 'lng': -87.62467861175537}], 'distance': 25, 'postalCode': '60661', 'cc': 'US', 'city': 'Chicago', 'state': 'IL', 'country': 'United States', 'formattedAddress': ['Citigroup Center (500 West Madison Street)', 'Chicago, IL 60661', 'United States']}, 'categories': [{'id': '4bf58dd8d48988d169941735', 'name': 'Australian Restaurant', 'pluralName': 'Australian Restaurants', 'shortName': 'Australian', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/australian_', 'suffix': '.png'}, 'primary': True}], 'referralId': 'v-1561410639', 'hasPerk': False}, {'id': '4aea34f2f964a52030ba21e3', 'name': 'CTA - Adams/Wabash', 'location':

{'meta': {'code': 200, 'requestId': '5d113c50c53093002cc04477'}, 'response': {'venues': [{'id': '54659f6f498e137569427d36', 'name': 'Metra  Food Court', 'location': {'address': 'Citigroup Center', 'crossStreet': '500 West Madison Street', 'lat': 41.875440756396515, 'lng': -87.62467861175537, 'labeledLatLngs': [{'label': 'display', 'lat': 41.875440756396515, 'lng': -87.62467861175537}], 'distance': 25, 'postalCode': '60661', 'cc': 'US', 'city': 'Chicago', 'state': 'IL', 'country': 'United States', 'formattedAddress': ['Citigroup Center (500 West Madison Street)', 'Chicago, IL 60661', 'United States']}, 'categories': [{'id': '4bf58dd8d48988d169941735', 'name': 'Australian Restaurant', 'pluralName': 'Australian Restaurants', 'shortName': 'Australian', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/australian_', 'suffix': '.png'}, 'primary': True}], 'referralId': 'v-1561410640', 'hasPerk': False}, {'id': '4aea34f2f964a52030ba21e3', 'name': 'CTA - Adams/Wabash', 'location':

{'meta': {'code': 200, 'requestId': '5d113c50dbde11002522d2fd'}, 'response': {'venues': [{'id': '54659f6f498e137569427d36', 'name': 'Metra  Food Court', 'location': {'address': 'Citigroup Center', 'crossStreet': '500 West Madison Street', 'lat': 41.875440756396515, 'lng': -87.62467861175537, 'labeledLatLngs': [{'label': 'display', 'lat': 41.875440756396515, 'lng': -87.62467861175537}], 'distance': 25, 'postalCode': '60661', 'cc': 'US', 'city': 'Chicago', 'state': 'IL', 'country': 'United States', 'formattedAddress': ['Citigroup Center (500 West Madison Street)', 'Chicago, IL 60661', 'United States']}, 'categories': [{'id': '4bf58dd8d48988d169941735', 'name': 'Australian Restaurant', 'pluralName': 'Australian Restaurants', 'shortName': 'Australian', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/australian_', 'suffix': '.png'}, 'primary': True}], 'referralId': 'v-1561410640', 'hasPerk': False}, {'id': '4aea34f2f964a52030ba21e3', 'name': 'CTA - Adams/Wabash', 'location':

{'meta': {'code': 200, 'requestId': '5d113c50d9a6e6002bc02329'}, 'response': {'venues': [{'id': '54659f6f498e137569427d36', 'name': 'Metra  Food Court', 'location': {'address': 'Citigroup Center', 'crossStreet': '500 West Madison Street', 'lat': 41.875440756396515, 'lng': -87.62467861175537, 'labeledLatLngs': [{'label': 'display', 'lat': 41.875440756396515, 'lng': -87.62467861175537}], 'distance': 25, 'postalCode': '60661', 'cc': 'US', 'city': 'Chicago', 'state': 'IL', 'country': 'United States', 'formattedAddress': ['Citigroup Center (500 West Madison Street)', 'Chicago, IL 60661', 'United States']}, 'categories': [{'id': '4bf58dd8d48988d169941735', 'name': 'Australian Restaurant', 'pluralName': 'Australian Restaurants', 'shortName': 'Australian', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/australian_', 'suffix': '.png'}, 'primary': True}], 'referralId': 'v-1561410640', 'hasPerk': False}, {'id': '4aea34f2f964a52030ba21e3', 'name': 'CTA - Adams/Wabash', 'location':

{'meta': {'code': 200, 'requestId': '5d113c510d2be7002cdecd51'}, 'response': {'venues': [{'id': '54659f6f498e137569427d36', 'name': 'Metra  Food Court', 'location': {'address': 'Citigroup Center', 'crossStreet': '500 West Madison Street', 'lat': 41.875440756396515, 'lng': -87.62467861175537, 'labeledLatLngs': [{'label': 'display', 'lat': 41.875440756396515, 'lng': -87.62467861175537}], 'distance': 25, 'postalCode': '60661', 'cc': 'US', 'city': 'Chicago', 'state': 'IL', 'country': 'United States', 'formattedAddress': ['Citigroup Center (500 West Madison Street)', 'Chicago, IL 60661', 'United States']}, 'categories': [{'id': '4bf58dd8d48988d169941735', 'name': 'Australian Restaurant', 'pluralName': 'Australian Restaurants', 'shortName': 'Australian', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/australian_', 'suffix': '.png'}, 'primary': True}], 'referralId': 'v-1561410641', 'hasPerk': False}, {'id': '4aea34f2f964a52030ba21e3', 'name': 'CTA - Adams/Wabash', 'location':

...

{'meta': {'code': 200, 'requestId': '5d113c76be7078002c07bd60'}, 'response': {'venues': [{'id': '54659f6f498e137569427d36', 'name': 'Metra  Food Court', 'location': {'address': 'Citigroup Center', 'crossStreet': '500 West Madison Street', 'lat': 41.875440756396515, 'lng': -87.62467861175537, 'labeledLatLngs': [{'label': 'display', 'lat': 41.875440756396515, 'lng': -87.62467861175537}], 'distance': 25, 'postalCode': '60661', 'cc': 'US', 'city': 'Chicago', 'state': 'IL', 'country': 'United States', 'formattedAddress': ['Citigroup Center (500 West Madison Street)', 'Chicago, IL 60661', 'United States']}, 'categories': [{'id': '4bf58dd8d48988d169941735', 'name': 'Australian Restaurant', 'pluralName': 'Australian Restaurants', 'shortName': 'Australian', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/australian_', 'suffix': '.png'}, 'primary': True}], 'referralId': 'v-1561410678', 'hasPerk': False}, {'id': '4aea34f2f964a52030ba21e3', 'name': 'CTA - Adams/Wabash', 'location':

{'meta': {'code': 200, 'requestId': '5d113c76018cbb002c7a0cf8'}, 'response': {'venues': [{'id': '54659f6f498e137569427d36', 'name': 'Metra  Food Court', 'location': {'address': 'Citigroup Center', 'crossStreet': '500 West Madison Street', 'lat': 41.875440756396515, 'lng': -87.62467861175537, 'labeledLatLngs': [{'label': 'display', 'lat': 41.875440756396515, 'lng': -87.62467861175537}], 'distance': 25, 'postalCode': '60661', 'cc': 'US', 'city': 'Chicago', 'state': 'IL', 'country': 'United States', 'formattedAddress': ['Citigroup Center (500 West Madison Street)', 'Chicago, IL 60661', 'United States']}, 'categories': [{'id': '4bf58dd8d48988d169941735', 'name': 'Australian Restaurant', 'pluralName': 'Australian Restaurants', 'shortName': 'Australian', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/australian_', 'suffix': '.png'}, 'primary': True}], 'referralId': 'v-1561410678', 'hasPerk': False}, {'id': '4aea34f2f964a52030ba21e3', 'name': 'CTA - Adams/Wabash', 'location':

{'meta': {'code': 200, 'requestId': '5d113c76018cbb002c7a0f4b'}, 'response': {'venues': [{'id': '54659f6f498e137569427d36', 'name': 'Metra  Food Court', 'location': {'address': 'Citigroup Center', 'crossStreet': '500 West Madison Street', 'lat': 41.875440756396515, 'lng': -87.62467861175537, 'labeledLatLngs': [{'label': 'display', 'lat': 41.875440756396515, 'lng': -87.62467861175537}], 'distance': 25, 'postalCode': '60661', 'cc': 'US', 'city': 'Chicago', 'state': 'IL', 'country': 'United States', 'formattedAddress': ['Citigroup Center (500 West Madison Street)', 'Chicago, IL 60661', 'United States']}, 'categories': [{'id': '4bf58dd8d48988d169941735', 'name': 'Australian Restaurant', 'pluralName': 'Australian Restaurants', 'shortName': 'Australian', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/australian_', 'suffix': '.png'}, 'primary': True}], 'referralId': 'v-1561410678', 'hasPerk': False}, {'id': '4aea34f2f964a52030ba21e3', 'name': 'CTA - Adams/Wabash', 'location':

{'meta': {'code': 200, 'requestId': '5d113c77db1d81002cf8e641'}, 'response': {'venues': [{'id': '54659f6f498e137569427d36', 'name': 'Metra  Food Court', 'location': {'address': 'Citigroup Center', 'crossStreet': '500 West Madison Street', 'lat': 41.875440756396515, 'lng': -87.62467861175537, 'labeledLatLngs': [{'label': 'display', 'lat': 41.875440756396515, 'lng': -87.62467861175537}], 'distance': 25, 'postalCode': '60661', 'cc': 'US', 'city': 'Chicago', 'state': 'IL', 'country': 'United States', 'formattedAddress': ['Citigroup Center (500 West Madison Street)', 'Chicago, IL 60661', 'United States']}, 'categories': [{'id': '4bf58dd8d48988d169941735', 'name': 'Australian Restaurant', 'pluralName': 'Australian Restaurants', 'shortName': 'Australian', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/australian_', 'suffix': '.png'}, 'primary': True}], 'referralId': 'v-1561410679', 'hasPerk': False}, {'id': '4aea34f2f964a52030ba21e3', 'name': 'CTA - Adams/Wabash', 'location':

no rating
7.1
no rating
no rating
no rating
no rating
no rating
no rating
no rating
no rating
no rating
no rating
no rating
[{'id': '54659f6f498e137569427d36', 'name': 'Metra  Food Court', 'type': 'Australian Restaurant', 'address': {'address': 'Citigroup Center', 'crossStreet': '500 West Madison Street', 'lat': 41.875440756396515, 'lng': -87.62467861175537, 'labeledLatLngs': [{'label': 'display', 'lat': 41.875440756396515, 'lng': -87.62467861175537}], 'distance': 25, 'postalCode': '60661', 'cc': 'US', 'city': 'Chicago', 'state': 'IL', 'country': 'United States', 'formattedAddress': ['Citigroup Center (500 West Madison Street)', 'Chicago, IL 60661', 'United States']}, 'rating': 'NA'}, {'id': '4aea34f2f964a52030ba21e3', 'name': 'CTA - Adams/Wabash', 'type': 'Metro Station', 'address': {'address': '201 S Wabash Ave', 'crossStreet': 'at E Adams St', 'lat': 41.879535659279895, 'lng': -87.62602839296079, 'labeledLatLngs': [{'label': 'display', 'lat': 41.879535659279895, 'lng': -87.626028392

In [27]:
from ast import literal_eval
# tranforming json file into a pandas dataframe library
from pandas.io.json import json_normalize

with open("C:/Users/shahd/Documents/Python/Restaurant_venues.json") as f:
    data = f.read()
python_dict = literal_eval(data)
aa = json.dumps(python_dict)
dum = json.loads(aa)
op = (dum['response']['venues'])
venues = dum['response']['venues']

# tranform venues into a dataframe
dataframe = json_normalize(venues)
dataframe.head()
# keep only columns that include venue name, and anything that is associated with location
filtered_columns = ['name', 'categories'] + [col for col in dataframe.columns if col.startswith('location.')] + ['id']
dataframe_filtered = dataframe.loc[:, filtered_columns]

# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

# filter the category for each row
dataframe_filtered['categories'] = dataframe_filtered.apply(get_category_type, axis=1)

# clean column names by keeping only last term
dataframe_filtered.columns = [column.split('.')[-1] for column in dataframe_filtered.columns]

dataframe_filtered

dataframe_filtered.name
#print(dataframe_filtered.categories)
print(dataframe_filtered.name)

0                   The Berghoff Restaurant
1                 Plymouth Restaurant & Bar
2                Exchequer Restaurant & Pub
3                           Sofi Restaurant
4     Chicago Curry House Indian Restaurant
5                      Luna Cafe Restaurant
6           Gazebo Restaurant at Grant Park
7                      Himalayan Restaurant
8                      Lord Gore Restaurant
9     Rawabi Grill Mediterranean Restaurant
10                   Amarit Thai Restaurant
11                             Miller's Pub
12                         G & G Restaurant
13               McKinlock Court Restaurant
14               HALO' Restaurant - Chicago
15                              Gino's East
16                       Dearborn Dentistry
17                          Plymouth Street
18                  La Cocina Mexican Grill
19              S.R.O. - Standing Room Only
20                                   Subway
21               Middle Eastern Restaurants
Name: name, dtype: object


In [4]:
latitude = 41.8763
longitude = -87.6282

Restaurant_map = folium.Map(location=[latitude, longitude], zoom_start=15) # generate map centred around Ecco

# add Ecco as a red circle mark
folium.features.CircleMarker(
    [latitude, longitude],
    radius=10,
    popup='HW Library',
    fill=True,
    color='red',
    fill_color='red',
    fill_opacity=0.6
).add_to(Restaurant_map)

# add popular spots to the map as blue circle markers
for lat, lng, label in zip(dataframe_filtered.lat, dataframe_filtered.lng, dataframe_filtered.categories):
    folium.features.CircleMarker(
        [lat, lng],
        radius=10,
        popup = folium.Popup(label, parse_html=True),
        fill=True,
        color='blue',
        fill_color='blue',
        fill_opacity=0.6
    ).add_to(Restaurant_map)

# display map
Restaurant_map


In [28]:
from ast import literal_eval
# tranforming json file into a pandas dataframe library
from pandas.io.json import json_normalize
with open("C:/Users/shahd/Documents/Python/vegan_venues.json") as f:
    data = f.read()
python_dict = literal_eval(data)
aa = json.dumps(python_dict)
dum = json.loads(aa)
op = (dum['response']['venues'])
venues = dum['response']['venues']

# tranform venues into a dataframe
dataframe = json_normalize(venues)
dataframe.head()
# keep only columns that include venue name, and anything that is associated with location
filtered_columns = ['name', 'categories'] + [col for col in dataframe.columns if col.startswith('location.')] + ['id']
dataframe_filtered = dataframe.loc[:, filtered_columns]

# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

# filter the category for each row
dataframe_filtered['categories'] = dataframe_filtered.apply(get_category_type, axis=1)

# clean column names by keeping only last term
dataframe_filtered.columns = [column.split('.')[-1] for column in dataframe_filtered.columns]

dataframe_filtered

dataframe_filtered.name

print(dataframe_filtered.name)


0                   Metra  Food Court
1                  CTA - Adams/Wabash
2     Coco's southern style soul food
3               Wabash Food & Liquors
4           Southern Pitch Food Truck
5                Japan Food Express 6
6                  Japan Food Express
7               Giordano's Food Truck
8            Hot Dog Fiend Food Truck
9            University Food Services
10            DePaul Center Cafeteria
11               Hat Trick Food Truck
12                           H&J Deli
Name: name, dtype: object


In [30]:
latitude = 41.8763
longitude = -87.6282

ChineseRestaurant_map = folium.Map(location=[latitude, longitude], zoom_start=15) # generate map centred around Ecco

# add Ecco as a red circle mark
folium.features.CircleMarker(
    [latitude, longitude],
    radius=10,
    popup='HW Library',
    fill=True,
    color='red',
    fill_color='red',
    fill_opacity=0.6
).add_to(ChineseRestaurant_map)

# add popular spots to the map as blue circle markers
for lat, lng, label in zip(dataframe_filtered.lat, dataframe_filtered.lng, dataframe_filtered.categories):
    folium.features.CircleMarker(
        [lat, lng],
        radius=10,
        popup = folium.Popup(label, parse_html=True),
        fill=True,
        color='blue',
        fill_color='blue',
        fill_opacity=0.6
    ).add_to(ChineseRestaurant_map)

# display map
ChineseRestaurant_map

In [31]:
with open("C:/Users/shahd/Documents/Python/vegan_venues.json") as f:
    data = f.read()
python_dict = literal_eval(data)
aa = json.dumps(python_dict)
dum = json.loads(aa)
op = (dum['response']['venues'])
venues = dum['response']['venues']

# tranform venues into a dataframe
dataframe = json_normalize(venues)
dataframe.head()
# keep only columns that include venue name, and anything that is associated with location
filtered_columns = ['name', 'categories'] + [col for col in dataframe.columns if col.startswith('location.')] + ['id']
dataframe_filtered = dataframe.loc[:, filtered_columns]

# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

# filter the category for each row
dataframe_filtered['categories'] = dataframe_filtered.apply(get_category_type, axis=1)

# clean column names by keeping only last term
dataframe_filtered.columns = [column.split('.')[-1] for column in dataframe_filtered.columns]
dataframe_filtered.name
dataframe_filtered

 #= [i['timestamp'] for i in data["data"]]
#values = [i['bytes'] for i in data['data']]

name                       categories  \
0                 Metra  Food Court            Australian Restaurant   
1                CTA - Adams/Wabash                    Metro Station   
2   Coco's southern style soul food  Southern / Soul Food Restaurant   
3             Wabash Food & Liquors                      Snack Place   
4         Southern Pitch Food Truck                       Food Truck   
5              Japan Food Express 6              Japanese Restaurant   
6                Japan Food Express              Japanese Restaurant   
7             Giordano's Food Truck                       Food Truck   
8          Hot Dog Fiend Food Truck                       Food Truck   
9          University Food Services                             Food   
10          DePaul Center Cafeteria                College Cafeteria   
11             Hat Trick Food Truck                       Food Truck   
12                         H&J Deli                    Deli / Bodega   

                   address  cc     city        country  \
0         Citigroup Center  US  Chicago  United States   
1         201 S Wabash Ave  US  Chicago  United States   
2           426 S Clark St  US  Chicago  United States   
3                  Jackson  US  Chicago  United States   
4                      NaN  US  Chicago  United States   
5        60 E Jackson Blvd  US  Chicago  United States   
6          111 E Wacker Dr  US  Chicago  United States   
7                      NaN  US  Chicago  United States   
8                      NaN  US  Chicago  United States   
9        315 S Plymouth Ct  US  Chicago  United States   
10  1 E Jackson Blvd Fl 11  US  Chicago  United States   
11                     NaN  US  Chicago  United States   
12            15 W Jackson  US  Chicago  United States   

                crossStreet  distance  \
0   500 West Madison Street        25   
1             at E Adams St       462   
2                       NaN       531   
3                    Wabash       327   
4                       NaN       287   
5                       NaN       327   
6                       NaN       334   
7                       NaN       306   
8                       NaN       488   
9                       NaN       454   
10             State Street       346   
11                      NaN       551   
12                      NaN       427   

                                     formattedAddress  \
0   [Citigroup Center (500 West Madison Street), C...   
1   [201 S Wabash Ave (at E Adams St), Chicago, IL...   
2   [426 S Clark St, Chicago, IL 60605, United Sta...   
3   [Jackson (Wabash), Chicago, IL 60603, United S...   
4                  [Chicago, IL 60608, United States]   
5   [60 E Jackson Blvd, Chicago, IL 60604, United ...   
6       [111 E Wacker Dr, Chicago, IL, United States]   
7                  [Chicago, IL 60611, United States]   
8                        [Chicago, IL, United States]   
9   [315 S Plymouth Ct, Chicago, IL 60604, United ...   
10  [1 E Jackson Blvd Fl 11 (State Street), Chicag...   
11                 [Chicago, IL 60604, United States]   
12   [15 W Jackson, Chicago, IL 60604, United States]   

                                       labeledLatLngs        lat        lng  \
0   [{'label': 'display', 'lat': 41.87544075639651...  41.875441 -87.624679   
1   [{'label': 'display', 'lat': 41.87953565927989...  41.879536 -87.626028   
2   [{'label': 'display', 'lat': 41.87632, 'lng': ...  41.876320 -87.630755   
3   [{'label': 'display', 'lat': 41.87823672870496...  41.878237 -87.626073   
4   [{'label': 'display', 'lat': 41.87797181687470...  41.877972 -87.625678   
5   [{'label': 'display', 'lat': 41.878392, 'lng':...  41.878392 -87.625487   
6   [{'label': 'display', 'lat': 41.878326, 'lng':...  41.878326 -87.626012   
7   [{'label': 'display', 'lat': 41.87809674790581...  41.878097 -87.625861   
8   [{'label': 'display', 'lat': 41.87994367448381...  41.879944 -87.624242   
9   [{'label': 'display', 'lat': 41.878138, '